# Insurance Claims - Fraud Detection
**Business case:**  
Insurance fraud is a huge problem in the industry. It's difficult to identify fraud claims. IHS is in a unique position to help the Auto Insurance industry with this problem.  

**Problem Statement:**  
Data is stored in different systems and its difficult to build analytics using multiple data sources. Copying data into a single platform is time consuming.  

**Business solution:**  
Use Azure blob storage to store different sources of data in a single platform. This allows data scientists / analysis to quickly analyze the data and generate reports to predict market trends and/or make financial decisions.  

**Technical Solution:**  
Use Databricks as a single platform to pull various sources of data from API endpoints, or batch dumps into Azure for further processing. ETL the CSV datasets into efficient Parquet formats for performant processing.

In this example, we will be working with some auto insurance data to demonstrate how we can create a predictive model that predicts if an insurance claim is fraudulent or not. This will be a Binary Classification task, and we will be creating a Decision Tree model.

With the prediction data, we are able to estimate what our total predicted fradulent claim amount is like, and zoom into various features such as a breakdown of predicted fraud count by insured hobbies - our model's best predictor.
      
We will cover the following steps to illustrate how we build a Machine Learning Pipeline:
* Data Import
* Data Exploration
* Data Processing
* Create Decision Tree Model
* Measuring Error Rate
* Model Tuning
* Zooming in on Prediction Data

## Data Import

First download [this csv file](https://raw.githubusercontent.com/jodb/sparkTestData/master/insurance_claims.csv) locally

The data used in this example was from a CSV file that was imported using the Tables UI. [Databases and Tables](https://docs.databricks.com/user-guide/tables.html)

After uploading the data using the UI, we can run SparkSQL queries against the table, or create a DataFrame from the table.  
In this example, we will create a Spark DataFrame.

Below is the code to get the data from Blob Storage. In this project, we showed 2 ways of uploading and using data in data bricks. 
1) Blob storage to data bricks(Azure portal)
2) Directly upload data into DBFS (Azure data bricks)

In [0]:
#dbutils.fs.mount(
  #source = "wasbs://data@blobstoragefinal.blob.core.windows.net",
  #mount_point = "/mnt/iotdata",
  #extra_configs = {"fs.azure.account.key.blobstoragefinal.blob.core.windows.net":dbutils.secrets.get(scope = "Insurance", key = "Insurance1")})

In [0]:
# python
filestorepath = spark.read.format("csv").load("/mnt/iotdata/export (2).csv",header="true")
display(filestorepath)

months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 137 34 413978 2000-06-04 00:00:00 IN 250/500 1000 1333.35 0 441716 MALE PhD prof-specialty board-games husband 0 -77000 2015-01-13 00:00:00 Multi-vehicle Collision Front Collision Minor Damage Police NY Springfield 5846 Weaver Drive 0 3 ? 0 0 ? 78650 21450 7150 50050 Nissan Pathfinder 2012 N 165 37 429027 1990-02-03 00:00:00 IL 100/300 1000 1137.03 0 603195 MALE Associate tech-support base-jumping unmarried 0 0 2015-02-27 00:00:00 Multi-vehicle Collision Front Collision Total Loss Police VA Columbus 3525 3rd Hwy 23 3 ? 2 2 YES 51590 9380 9380 32830 Audi A5 2015 N 27 33 485665 1997-02-05 00:00:00 IL 100/300 500 1442.99 0 601734 FEMALE PhD other-service golf own-child 0 0 2015-01-30 00:00:00 Single Vehicle Collision Front Collision Total Loss Police WV Arlington 4872 Rock Ridge 21 1 NO 1 1 YES 27700 2770 2770 22160 Toyota Camry 2012 N 212 42 636550 2011-07-25 00:00:00 IL 100/300 500 1315.68 0 600983 MALE PhD priv-house-serv camping wife 0 -39300 2015-01-05 00:00:00 Single Vehicle Collision Rear Collision Total Loss Other NC Hillsdale 3066 Francis Ave 14 1 NO 2 1 ? 42300 4700 4700 32900 Saab 92x 1996 N 235 42 543610 2002-05-26 00:00:00 OH 100/300 500 1253.12 4000000 462283 FEMALE Masters exec-managerial dancing other-relative 38400 0 2015-01-06 00:00:00 Single Vehicle Collision Front Collision Total Loss Police NY Northbend 1558 1st Ridge 22 1 YES 2 2 ? 87010 7910 15820 63280 Ford F150 2002 N 447 61 214618 1999-05-29 00:00:00 OH 100/300 2000 1137.16 0 615561 FEMALE High School exec-managerial skydiving other-relative 0 -51000 2015-02-15 00:00:00 Multi-vehicle Collision Front Collision Major Damage Fire SC Springfield 5971 5th Hwy 21 3 YES 1 2 YES 114920 17680 17680 79560 Audi A3 2006 N 60 23 842

In [0]:
display(dbutils.fs.ls("/FileStore/tables/export__2_-2.csv"))

path name size dbfs:/FileStore/tables/export__2_-2.csv export__2_-2.csv 283959

In [0]:
dbutils.fs.refreshMounts()

Mounts successfully refreshed.
Out[70]: True

In [0]:
# data = spark.table("insurance_claims")
#data=filestorepath

fileStorePath = "/FileStore/tables/export__2_-2.csv"

data = spark.read.format("csv")\
          .options(inferSchema="true", header="true")\
          .load(fileStorePath)\
          .drop("_c39")
      
      
df = data.withColumn("policy_bind_date", data.policy_bind_date.cast("string"))\
         .withColumn("incident_date", data.incident_date.cast("string"))

In [0]:
# Preview data
display(df)

months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 137 34 413978 2000-06-04 00:00:00 IN 250/500 1000 1333.35 0 441716 MALE PhD prof-specialty board-games husband 0 -77000 2015-01-13 00:00:00 Multi-vehicle Collision Front Collision Minor Damage Police NY Springfield 5846 Weaver Drive 0 3 ? 0 0 ? 78650 21450 7150 50050 Nissan Pathfinder 2012 N 165 37 429027 1990-02-03 00:00:00 IL 100/300 1000 1137.03 0 603195 MALE Associate tech-support base-jumping unmarried 0 0 2015-02-27 00:00:00 Multi-vehicle Collision Front Collision Total Loss Police VA Columbus 3525 3rd Hwy 23 3 ? 2 2 YES 51590 9380 9380 32830 Audi A5 2015 N 27 33 485665 1997-02-05 00:00:00 IL 100/300 500 1442.99 0 601734 FEMALE PhD other-service golf own-child 0 0 2015-01-30 00:00:00 Single Vehicle Collision Front Collision Total Loss Police WV Arlington 4872 Rock Ridge 21 1 NO 1 1 YES 27700 2770 2770 22160 Toyota Camry 2012 N 212 42 636550 2011-07-25 00:00:00 IL 100/300 500 1315.68 0 600983 MALE PhD priv-house-serv camping wife 0 -39300 2015-01-05 00:00:00 Single Vehicle Collision Rear Collision Total Loss Other NC Hillsdale 3066 Francis Ave 14 1 NO 2 1 ? 42300 4700 4700 32900 Saab 92x 1996 N 235 42 543610 2002-05-26 00:00:00 OH 100/300 500 1253.12 4000000 462283 FEMALE Masters exec-managerial dancing other-relative 38400 0 2015-01-06 00:00:00 Single Vehicle Collision Front Collision Total Loss Police NY Northbend 1558 1st Ridge 22 1 YES 2 2 ? 87010 7910 15820 63280 Ford F150 2002 N 447 61 214618 1999-05-29 00:00:00 OH 100/300 2000 1137.16 0 615561 FEMALE High School exec-managerial skydiving other-relative 0 -51000 2015-02-15 00:00:00 Multi-vehicle Collision Front Collision Major Damage Fire SC Springfield 5971 5th Hwy 21 3 YES 1 2 YES 114920 17680 17680 79560 Audi A3 2006 N 60 23 842

## Data Exploration

We have several string (categorical) columns in our dataset, along with some ints and doubles.

In [0]:
display(df.dtypes)

_1 _2 months_as_customer int age int policy_number int policy_bind_date string policy_state string policy_csl string policy_deductable int policy_annual_premium double umbrella_limit int insured_zip int insured_sex string insured_education_level string insured_occupation string insured_hobbies string insured_relationship string capital-gains int capital-loss int incident_date string incident_type string collision_type string incident_severity string authorities_contacted string incident_state string incident_city string incident_location string incident_hour_of_the_day int number_of_vehicles_involved int property_damage string bodily_injuries int witnesses int police_report_available string total_claim_amount int injury_claim int property_claim int vehicle_claim int auto_make string auto_model string auto_year int fraud_reported string

Count number of categories for every categorical column (Count Distinct).

In [0]:
# Create a List of Column Names with data type = string
stringColList = [i[0] for i in df.dtypes if i[1] == 'string']
print (stringColList)

['policy_bind_date', 'policy_state', 'policy_csl', 'insured_sex', 'insured_education_level', 'insured_occupation', 'insured_hobbies', 'insured_relationship', 'incident_date', 'incident_type', 'collision_type', 'incident_severity', 'authorities_contacted', 'incident_state', 'incident_city', 'incident_location', 'property_damage', 'police_report_available', 'auto_make', 'auto_model', 'fraud_reported']

In [0]:
from pyspark.sql.functions import *

# Create a function that performs a countDistinct(colName)
distinctList = []
def countDistinctCats(colName):
  count = df.agg(countDistinct(colName)).collect()
  distinctList.append(count)


In [0]:
# Apply function on every column in stringColList
map(countDistinctCats, stringColList)
print (distinctList)

[]

We have identified that some string columns have many distinct values (900+). We will remove these columns from our dataset in the Data Processing step to improve model accuracy.
* policy number (1000 distinct)
* policy bind date (951 distinct. Possible to narrow down to year/month to test model accuracy)
* insured zip (995 distinct)
* insured location (1000 distinct)
* incident date (60 distinct. Excluding, but possible to narrow down to year/month to test model accuracy)

Like most fraud datasets, our label distribution is skewed.

In [0]:
display(df)

months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 137 34 413978 2000-06-04 00:00:00 IN 250/500 1000 1333.35 0 441716 MALE PhD prof-specialty board-games husband 0 -77000 2015-01-13 00:00:00 Multi-vehicle Collision Front Collision Minor Damage Police NY Springfield 5846 Weaver Drive 0 3 ? 0 0 ? 78650 21450 7150 50050 Nissan Pathfinder 2012 N 165 37 429027 1990-02-03 00:00:00 IL 100/300 1000 1137.03 0 603195 MALE Associate tech-support base-jumping unmarried 0 0 2015-02-27 00:00:00 Multi-vehicle Collision Front Collision Total Loss Police VA Columbus 3525 3rd Hwy 23 3 ? 2 2 YES 51590 9380 9380 32830 Audi A5 2015 N 27 33 485665 1997-02-05 00:00:00 IL 100/300 500 1442.99 0 601734 FEMALE PhD other-service golf own-child 0 0 2015-01-30 00:00:00 Single Vehicle Collision Front Collision Total Loss Police WV Arlington 4872 Rock Ridge 21 1 NO 1 1 YES 27700 2770 2770 22160 Toyota Camry 2012 N 212 42 636550 2011-07-25 00:00:00 IL 100/300 500 1315.68 0 600983 MALE PhD priv-house-serv camping wife 0 -39300 2015-01-05 00:00:00 Single Vehicle Collision Rear Collision Total Loss Other NC Hillsdale 3066 Francis Ave 14 1 NO 2 1 ? 42300 4700 4700 32900 Saab 92x 1996 N 235 42 543610 2002-05-26 00:00:00 OH 100/300 500 1253.12 4000000 462283 FEMALE Masters exec-managerial dancing other-relative 38400 0 2015-01-06 00:00:00 Single Vehicle Collision Front Collision Total Loss Police NY Northbend 1558 1st Ridge 22 1 YES 2 2 ? 87010 7910 15820 63280 Ford F150 2002 N 447 61 214618 1999-05-29 00:00:00 OH 100/300 2000 1137.16 0 615561 FEMALE High School exec-managerial skydiving other-relative 0 -51000 2015-02-15 00:00:00 Multi-vehicle Collision Front Collision Major Damage Fire SC Springfield 5971 5th Hwy 21 3 YES 1 2 YES 114920 17680 17680 79560 Audi A3 2006 N 60 23 842

In [0]:
# Count number of frauds vs non-frauds
display(df.groupBy("fraud_reported").count())

fraud_reported count Y 247 N 753

We can quickly create one-click plots using Databricks built-in visualizations to understand our data better.

In [0]:
# Fraud Count by Incident State
display(df)

months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 137 34 413978 2000-06-04 00:00:00 IN 250/500 1000 1333.35 0 441716 MALE PhD prof-specialty board-games husband 0 -77000 2015-01-13 00:00:00 Multi-vehicle Collision Front Collision Minor Damage Police NY Springfield 5846 Weaver Drive 0 3 ? 0 0 ? 78650 21450 7150 50050 Nissan Pathfinder 2012 N 165 37 429027 1990-02-03 00:00:00 IL 100/300 1000 1137.03 0 603195 MALE Associate tech-support base-jumping unmarried 0 0 2015-02-27 00:00:00 Multi-vehicle Collision Front Collision Total Loss Police VA Columbus 3525 3rd Hwy 23 3 ? 2 2 YES 51590 9380 9380 32830 Audi A5 2015 N 27 33 485665 1997-02-05 00:00:00 IL 100/300 500 1442.99 0 601734 FEMALE PhD other-service golf own-child 0 0 2015-01-30 00:00:00 Single Vehicle Collision Front Collision Total Loss Police WV Arlington 4872 Rock Ridge 21 1 NO 1 1 YES 27700 2770 2770 22160 Toyota Camry 2012 N 212 42 636550 2011-07-25 00:00:00 IL 100/300 500 1315.68 0 600983 MALE PhD priv-house-serv camping wife 0 -39300 2015-01-05 00:00:00 Single Vehicle Collision Rear Collision Total Loss Other NC Hillsdale 3066 Francis Ave 14 1 NO 2 1 ? 42300 4700 4700 32900 Saab 92x 1996 N 235 42 543610 2002-05-26 00:00:00 OH 100/300 500 1253.12 4000000 462283 FEMALE Masters exec-managerial dancing other-relative 38400 0 2015-01-06 00:00:00 Single Vehicle Collision Front Collision Total Loss Police NY Northbend 1558 1st Ridge 22 1 YES 2 2 ? 87010 7910 15820 63280 Ford F150 2002 N 447 61 214618 1999-05-29 00:00:00 OH 100/300 2000 1137.16 0 615561 FEMALE High School exec-managerial skydiving other-relative 0 -51000 2015-02-15 00:00:00 Multi-vehicle Collision Front Collision Major Damage Fire SC Springfield 5971 5th Hwy 21 3 YES 1 2 YES 114920 17680 17680 79560 Audi A3 2006 N 60 23 842

In [0]:
# Breakdown of Average Vehicle claim by insured's education level, grouped by fraud reported
display(df)

months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 137 34 413978 2000-06-04 00:00:00 IN 250/500 1000 1333.35 0 441716 MALE PhD prof-specialty board-games husband 0 -77000 2015-01-13 00:00:00 Multi-vehicle Collision Front Collision Minor Damage Police NY Springfield 5846 Weaver Drive 0 3 ? 0 0 ? 78650 21450 7150 50050 Nissan Pathfinder 2012 N 165 37 429027 1990-02-03 00:00:00 IL 100/300 1000 1137.03 0 603195 MALE Associate tech-support base-jumping unmarried 0 0 2015-02-27 00:00:00 Multi-vehicle Collision Front Collision Total Loss Police VA Columbus 3525 3rd Hwy 23 3 ? 2 2 YES 51590 9380 9380 32830 Audi A5 2015 N 27 33 485665 1997-02-05 00:00:00 IL 100/300 500 1442.99 0 601734 FEMALE PhD other-service golf own-child 0 0 2015-01-30 00:00:00 Single Vehicle Collision Front Collision Total Loss Police WV Arlington 4872 Rock Ridge 21 1 NO 1 1 YES 27700 2770 2770 22160 Toyota Camry 2012 N 212 42 636550 2011-07-25 00:00:00 IL 100/300 500 1315.68 0 600983 MALE PhD priv-house-serv camping wife 0 -39300 2015-01-05 00:00:00 Single Vehicle Collision Rear Collision Total Loss Other NC Hillsdale 3066 Francis Ave 14 1 NO 2 1 ? 42300 4700 4700 32900 Saab 92x 1996 N 235 42 543610 2002-05-26 00:00:00 OH 100/300 500 1253.12 4000000 462283 FEMALE Masters exec-managerial dancing other-relative 38400 0 2015-01-06 00:00:00 Single Vehicle Collision Front Collision Total Loss Police NY Northbend 1558 1st Ridge 22 1 YES 2 2 ? 87010 7910 15820 63280 Ford F150 2002 N 447 61 214618 1999-05-29 00:00:00 OH 100/300 2000 1137.16 0 615561 FEMALE High School exec-managerial skydiving other-relative 0 -51000 2015-02-15 00:00:00 Multi-vehicle Collision Front Collision Major Damage Fire SC Springfield 5971 5th Hwy 21 3 YES 1 2 YES 114920 17680 17680 79560 Audi A3 2006 N 60 23 842

## Data Processing

Next, we will clean up the data a little and prepare it for our machine learning model.

We will first remove the columns that we have identified earlier that have too many distinct categories and cannot be converted to numeric.

In [0]:
colsToDelete = ["policy_number", "policy_bind_date", "insured_zip", "incident_location", "incident_date"]
filteredStringColList = [i for i in stringColList if i not in colsToDelete]

%md We will convert categorical columns to numeric to pass them into various algorithms. This can be done using the StringIndexer.

Here, we are generating a StringIndexer for each categorical column and appending it as a stage of our ML Pipeline.

In [0]:
from pyspark.ml.feature import StringIndexer

transformedCols = [categoricalCol + "Index" for categoricalCol in filteredStringColList]
stages = [StringIndexer(inputCol = categoricalCol, outputCol = categoricalCol + "Index") for categoricalCol in filteredStringColList]
stages

Out[82]: [StringIndexer_30109e8c58de,
 StringIndexer_aed632bcc1af,
 StringIndexer_aa12021ee151,
 StringIndexer_a6170e10d871,
 StringIndexer_5e835d307a70,
 StringIndexer_4e8d22e0d075,
 StringIndexer_1961ae6b238d,
 StringIndexer_434efda41898,
 StringIndexer_2fc683ba29da,
 StringIndexer_f97d6085fb36,
 StringIndexer_6f52b20e389a,
 StringIndexer_94b51ff363a7,
 StringIndexer_5129a448ac8d,
 StringIndexer_f2b0f5364384,
 StringIndexer_44fb91c702bf,
 StringIndexer_9b8a3154757f,
 StringIndexer_5e3f1f8b82c4,
 StringIndexer_c8eff6a7df6e]

As an example, this is what the transformed dataset will look like after applying the StringIndexer on all categorical columns.

In [0]:
from pyspark.ml import Pipeline

indexer = Pipeline(stages=stages)
indexed = indexer.fit(df).transform(df)
display(indexed)

months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported policy_stateIndex policy_cslIndex insured_sexIndex insured_education_levelIndex insured_occupationIndex insured_hobbiesIndex insured_relationshipIndex incident_typeIndex collision_typeIndex incident_severityIndex authorities_contactedIndex incident_stateIndex incident_cityIndex property_damageIndex police_report_availableIndex auto_makeIndex auto_modelIndex fraud_reportedIndex 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 0.0 0.0 1.0 3.0 5.0 17.0 3.0 1.0 1.0 2.0 0.0 1.0 2.0 2.0 2.0 1.0 11.0 1.0 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 2.0 0.0 1.0 3.0 0.0 0.0 1.0 2.0 3.0 0.0 0.0 4.0 5.0 0.0 0.0 12.0 15.0 1.0 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 0.0 1.0 0.0 5.0 4.0 13.0 0.0 0.0 0.0 0.0 0.0 0.0 2.0 1.0 1.0 0.0 0.0 0.0 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 1.0 0.0 0.0 5.0 9.0 13.0 5.0 1.0 2.0 2.0 0.0 6.0 1.0 0.0 1.0 4.0 21.0 1.0 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 1.0 2.0 1.0 2.0 4.0 13.0 5.0 2.0 3.0 0.0 4.0 0.0 1.0 1.0 1.0 9.0 38.0 0.0 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 0.0 0.0 0.0 5.0 2.0 3.0 5.0 0.0 0.0 2.0 1.0 1.0 1.0 1.0 1.0 1.0 14.0 1.0 137 34 413978 2000-06-04 00:00:00 IN 250/500 1000 1333.35 0 441716 MALE PhD prof-specialty board-games husband 0 -77000 2015-01-13 00:00:00 Multi-vehicle Collision Front Collision Minor Damage Police NY Springfield 5846 Weaver Drive 0 3 ? 0 0 ? 78650 21450 7150 50050 Nissan Pathfinder 2012 N 2.0 0.0 1.0 5.0 1.0 13.0 3.0 0.0 2.0 0.0 0.0 0.0 0.0 0.0 0.0 3.0 9.0 0.0 165 37 429027 1990-02-03 00:00:00 IL 100/300 1000 1137.03 0 603195 MALE Associate tech-support base-jumping unmarried 0 0 2015-02-27 00:00:00 Multi-vehicle Collision Front Collision Total Loss Police VA Columbus 3525 3rd Hwy 23 3 ? 2 2 YES 51590 9380 9380 32830 Audi A5 2015 N 1.0 1.0 1.0 2.0 2.0 11.0 5.0 0.0 2.0 1.0 0.0 4.0 2.0 0.0 2.0 8.0 7.0 0.0 27 33 485665 1997-02-05 00:00:00 IL 100/300 500 1442.99 0 601734 FEMALE PhD other-service golf own-child 0 0 2015-01-30 00:00:00 Single Vehicle Collision Front Collision Total Loss Po

Use the VectorAssembler to combine all the feature columns into a single vector column. This will include both the numeric columns and the indexed categorical columns.

In [0]:
from pyspark.ml.feature import VectorAssembler

# In this dataset, numericColList will contain columns of type Int and Double
numericColList = [i[0] for i in df.dtypes if i[1] != 'string']
assemblerInputs = list(map(lambda c: c + "Index", filteredStringColList)) + numericColList

# Remove label from list of features
label = "fraud_reportedIndex"
assemblerInputs.remove(label)
assemblerInputs
assembler = VectorAssembler(inputCols=assemblerInputs, outputCol="features")

# Append assembler to stages, which currently contains the StringIndexer transformers
stages += [assembler]

Generate transformed dataset. This will be the dataset that we will use to create our machine learning models.

In [0]:
pipeline = Pipeline(stages=stages)
pipelineModel = pipeline.fit(df)
transformed_df = pipelineModel.transform(df)

# Rename label column
transformed_df = transformed_df.withColumnRenamed('fraud_reportedIndex', 'label')

# Keep relevant columns (original columns, features, labels)
originalCols = df.columns
selectedcols = ["label", "fraud_reported", "features"] + originalCols
dataset = transformed_df.select(selectedcols)
display(dataset)

label fraud_reported features months_as_customer age policy_number policy_bind_date policy_state policy_csl policy_deductable policy_annual_premium umbrella_limit insured_zip insured_sex insured_education_level insured_occupation insured_hobbies insured_relationship capital-gains capital-loss incident_date incident_type collision_type incident_severity authorities_contacted incident_state incident_city incident_location incident_hour_of_the_day number_of_vehicles_involved property_damage bodily_injuries witnesses police_report_available total_claim_amount injury_claim property_claim vehicle_claim auto_make auto_model auto_year fraud_reported 1.0 Y List(1, 35, List(), List(0.0, 0.0, 1.0, 3.0, 5.0, 17.0, 3.0, 1.0, 1.0, 2.0, 0.0, 1.0, 2.0, 2.0, 2.0, 1.0, 11.0, 328.0, 48.0, 521585.0, 1000.0, 1406.91, 0.0, 466132.0, 53300.0, 0.0, 5.0, 1.0, 1.0, 2.0, 71610.0, 6510.0, 13020.0, 52080.0, 2004.0)) 328 48 521585 2014-10-17 00:00:00 OH 250/500 1000 1406.91 0 466132 MALE MD craft-repair sleeping husband 53300 0 2015-01-25 00:00:00 Single Vehicle Collision Side Collision Major Damage Police SC Columbus 9935 4th Drive 5 1 YES 1 2 YES 71610 6510 13020 52080 Saab 92x 2004 Y 1.0 Y List(1, 35, List(), List(2.0, 0.0, 1.0, 3.0, 0.0, 0.0, 1.0, 2.0, 3.0, 0.0, 0.0, 4.0, 5.0, 0.0, 0.0, 12.0, 15.0, 228.0, 42.0, 342868.0, 2000.0, 1197.22, 5000000.0, 468176.0, 0.0, 0.0, 8.0, 1.0, 0.0, 0.0, 5070.0, 780.0, 780.0, 3510.0, 2007.0)) 228 42 342868 2006-06-27 00:00:00 IN 250/500 2000 1197.22 5000000 468176 MALE MD machine-op-inspct reading other-relative 0 0 2015-01-21 00:00:00 Vehicle Theft ? Minor Damage Police VA Riverwood 6608 MLK Hwy 8 1 ? 0 0 ? 5070 780 780 3510 Mercedes E400 2007 Y 0.0 N List(1, 35, List(), List(0.0, 1.0, 0.0, 5.0, 4.0, 13.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 1.0, 1.0, 0.0, 0.0, 134.0, 29.0, 687698.0, 2000.0, 1413.14, 5000000.0, 430632.0, 35100.0, 0.0, 7.0, 3.0, 2.0, 3.0, 34650.0, 7700.0, 3850.0, 23100.0, 2007.0)) 134 29 687698 2000-09-06 00:00:00 OH 100/300 2000 1413.14 5000000 430632 FEMALE PhD sales board-games own-child 35100 0 2015-02-22 00:00:00 Multi-vehicle Collision Rear Collision Minor Damage Police NY Columbus 7121 Francis Lane 7 3 NO 2 3 NO 34650 7700 3850 23100 Dodge RAM 2007 N 1.0 Y List(1, 35, List(), List(1.0, 0.0, 0.0, 5.0, 9.0, 13.0, 5.0, 1.0, 2.0, 2.0, 0.0, 6.0, 1.0, 0.0, 1.0, 4.0, 21.0, 256.0, 41.0, 227811.0, 2000.0, 1415.74, 6000000.0, 608117.0, 48900.0, -62400.0, 5.0, 1.0, 1.0, 2.0, 63400.0, 6340.0, 6340.0, 50720.0, 2014.0)) 256 41 227811 1990-05-25 00:00:00 IL 250/500 2000 1415.74 6000000 608117 FEMALE PhD armed-forces board-games unmarried 48900 -62400 2015-01-10 00:00:00 Single Vehicle Collision Front Collision Major Damage Police OH Arlington 6956 Maple Drive 5 1 ? 1 2 NO 63400 6340 6340 50720 Chevrolet Tahoe 2014 Y 0.0 N List(1, 35, List(), List(1.0, 2.0, 1.0, 2.0, 4.0, 13.0, 5.0, 2.0, 3.0, 0.0, 4.0, 0.0, 1.0, 1.0, 1.0, 9.0, 38.0, 228.0, 44.0, 367455.0, 1000.0, 1583.91, 6000000.0, 610706.0, 66000.0, -46000.0, 20.0, 1.0, 0.0, 1.0, 6500.0, 1300.0, 650.0, 4550.0, 2009.0)) 228 44 367455 2014-06-06 00:00:00 IL 500/1000 1000 1583.91 6000000 610706 MALE Associate sales board-games unmarried 66000 -46000 2015-02-17 00:00:00 Vehicle Theft ? Minor Damage None NY Arlington 3041 3rd Ave 20 1 NO 0 1 NO 6500 1300 650 4550 Accura RSX 2009 N 1.0 Y List(1, 35, List(), List(0.0, 0.0, 0.0, 5.0, 2.0, 3.0, 5.0, 0.0, 0.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 14.0, 256.0, 39.0, 104594.0, 1000.0, 1351.1, 0.0, 478456.0, 0.0, 0.0, 19.0, 3.0, 0.0, 2.0, 64100.0, 6410.0, 6410.0, 51280.0, 2003.0)) 256 39 104594 2006-10-12 00:00:00 OH 250/500 1000 1351.1 0 478456 FEMALE PhD tech-support bungie-jumping unmarried 0 0 2015-01-02 00:00:00 Multi-vehicle Collision Rear Collision Major Damage Fire SC Arlington 8973 Washington St 19 3 NO 0 2 NO 64100 6410 6410 51280 Saab 95 2003 Y 0.0 N List(0, 35, List(0, 2, 3, 4, 5, 6, 8, 15, 16, 17, 18, 19, 20, 21, 23, 25, 27, 30, 31, 32, 33, 34), List(2.0, 1.0, 5.0, 1.0, 13.0, 3.0, 2.0, 3.0, 9.0, 137.0, 34.0, 413

By selecting "label" and "fraud reported", we can infer that 0 corresponds to **No Fraud Reported** and 1 corresponds to **Fraud Reported**.

Next, split data into training and test sets.

In [0]:
### Randomly split data into training and test sets. set seed for reproducibility
(trainingData, testData) = dataset.randomSplit([0.7, 0.3], seed = 100)
print (trainingData.count())
print (testData.count())

703
297

Databricks makes it easy to use multiple languages in the same notebook for your analyses. Just register your dataset as a temporary table and you can access it using a different language!

In [0]:
# Register data as temp table to jump to Scala
trainingData.createOrReplaceTempView("trainingData")
testData.createOrReplaceTempView("testData")

## Create Decision Tree Model

We will create a decision tree model in Scala using the trainingData. This will be our initial model.

In [0]:
%scala

import org.apache.spark.ml.classification.{DecisionTreeClassifier, DecisionTreeClassificationModel}

// Create DataFrames using our earlier registered temporary tables
val trainingData = spark.table("trainingData")
val testData = spark.table("testData")

// Create initial Decision Tree Model
val dt = new DecisionTreeClassifier()
  .setLabelCol("label")
  .setFeaturesCol("features")
  .setMaxDepth(5)
  .setMaxBins(40)

// Train model with Training Data
val dtModel = dt.fit(trainingData)

import org.apache.spark.ml.classification.{DecisionTreeClassifier, DecisionTreeClassificationModel}
trainingData: org.apache.spark.sql.DataFrame = [label: double, fraud_reported: string ... 40 more fields]
testData: org.apache.spark.sql.DataFrame = [label: double, fraud_reported: string ... 40 more fields]
dt: org.apache.spark.ml.classification.DecisionTreeClassifier = dtc_5f9b0110aad5
dtModel: org.apache.spark.ml.classification.DecisionTreeClassificationModel = DecisionTreeClassificationModel: uid=dtc_5f9b0110aad5, depth=5, numNodes=39, numClasses=2, numFeatures=35

In [0]:
%scala

// Make predictions on test data using the transform() method.
// .transform() will only use the 'features' column as input.
val dtPredictions = dtModel.transform(testData)

dtPredictions: org.apache.spark.sql.DataFrame = [label: double, fraud_reported: string ... 43 more fields]

In [0]:
%scala

// View model's predictions and probabilities of each prediction class
val selected = dtPredictions.select("label", "prediction", "probability")
display(selected)

label prediction probability 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 1.0 List(1, 2, List(), List(0.3333333333333333, 0.6666666666666666)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.16129032258064516, 0.8387096774193549)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 1.0 List(1, 2, List(), List(0.14285714285714285, 0.8571428571428571)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.3157894736842105, 0.6842105263157895)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.3157894736842105, 0.6842105263157895)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.3333333333333333, 0.6666666666666666)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(0.9090909090909091, 0.09090909090909091)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.3333333333333333, 0.6666666666666666)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(0.8333333333333334, 0.16666666666666666)) 0.0 1.0 List(1, 2, List(), List(0.05714285714285714, 0.9428571428571428)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.16129032258064516, 0.8387096774193549)) 0.0 0.0 List(1, 2, List(), List(0.9090909090909091, 0.09090909090909091)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.05714285714285714, 0.9428571428571428)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.14285714285714285, 0.8571428571428571)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 1.0 List(1, 2, List(), List(0.16129032258064516, 0.8387096774193549)) 0.0 0.0 List(1, 2, List(), List(0.9295774647887324, 0.07042253521126761)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 0.0 List(1, 2, List(), List(1.0, 0.0)) 0.0 1.0 List(1, 2, List(), List(0.16129032258064516, 0.

## Measuring Error Rate

Evaluate our initial model using the BinaryClassificationEvaluator.

In [0]:
%scala

import org.apache.spark.ml.evaluation.BinaryClassificationEvaluator

// Evaluate model

val evaluator = new BinaryClassificationEvaluator()
evaluator.evaluate(dtPredictions)

import org.apache.spark.ml.evaluation.BinaryClassificationEvaluator
evaluator: org.apache.spark.ml.evaluation.BinaryClassificationEvaluator = BinaryClassificationEvaluator: uid=binEval_a93c578d7202, metricName=areaUnderROC, numBins=1000
res36: Double = 0.7465725806451613

## Model Tuning

We can tune our models using built-in libraries like `ParamGridBuilder` for Grid Search, and `CrossValidator` for Cross Validation. In this example, we will test out a combination of Grid Search with 5-fold Cross Validation.  

Here, we will see if we can improve accuracy rates from our initial model.

In [0]:
%scala

// View tunable parameters for Decision Trees
dt.explainParams

res37: String =
cacheNodeIds: If false, the algorithm will pass trees to executors to match instances with nodes. If true, the algorithm will cache node IDs for each instance. Caching can speed up training of deeper trees. (default: false)
checkpointInterval: set checkpoint interval (>= 1) or disable checkpoint (-1). E.g. 10 means that the cache will get checkpointed every 10 iterations. Note: this setting will be ignored if the checkpoint directory is not set in the SparkContext (default: 10)
featuresCol: features column name (default: features, current: features)
impurity: Criterion used for information gain calculation (case-insensitive). Supported options: entropy, gini (default: gini)
labelCol: label column name (default: label, current: label)
leafCol: Leaf indices column name. Predicted leaf index of each instance in each tree by preorder (default: )
maxBins: Max number of bins for discretizing continuous features. Must be at least 2 and at least number of categories for any categorical feature. (default: 32, current: 40)
maxDepth: Maximum depth of the tree. (Nonnegative) E.g., depth 0 means 1 leaf node; depth 1 means 1 internal node + 2 leaf nodes. (default: 5, current: 5)
maxMemoryInMB: Maximum memory in MB allocated to histogram aggregation. (default: 256)
minInfoGain: Minimum information gain for a split to be considered at a tree node. (default: 0.0)
minInstancesPerNode: Minimum number of instances each child must have after split. If a split causes the left or right child to have fewer than minInstancesPerNode, the split will be discarded as invalid. Must be at least 1. (default: 1)
minWeightFractionPerNode: Minimum fraction of the weighted sample count that each child must have after split. If a split causes the fraction of the total weight in the left or right child to be less than minWeightFractionPerNode, the split will be discarded as invalid. Should be in interval [0.0, 0.5) (default: 0.0)
predictionCol: prediction column name (default: prediction)
probabilityCol: Column name for predicted class conditional probabilities. Note: Not all models output well-calibrated probability estimates! These probabilities should be treated as confidences, not precise probabilities (default: probability)
rawPredictionCol: raw prediction (a.k.a. confidence) column name (default: rawPrediction)
seed: random seed (default: 159147643)
thresholds: Thresholds in multi-class classification to adjust the probability of predicting each class. Array must have length equal to the number of classes, with values > 0 excepting that at most one value may be 0. The class with largest value p/t is predicted, where p is the original probability of that class and t is the class's threshold (undefined)
weightCol: weight column name. If this is not set or empty, we treat all instance weights as 1.0 (undefined)

Create a ParamGrid to perform Grid Search. We will be adding various values of maxDepth and maxBins.

In [0]:
%scala

import org.apache.spark.ml.tuning.{ParamGridBuilder, CrossValidator}

val paramGrid = new ParamGridBuilder()
  .addGrid(dt.maxDepth, Array(3, 10, 15))
  .addGrid(dt.maxBins, Array(40, 50))
  .build()

import org.apache.spark.ml.tuning.{ParamGridBuilder, CrossValidator}
paramGrid: Array[org.apache.spark.ml.param.ParamMap] =
Array({
	dtc_5f9b0110aad5-maxBins: 40,
	dtc_5f9b0110aad5-maxDepth: 3
}, {
	dtc_5f9b0110aad5-maxBins: 40,
	dtc_5f9b0110aad5-maxDepth: 10
}, {
	dtc_5f9b0110aad5-maxBins: 40,
	dtc_5f9b0110aad5-maxDepth: 15
}, {
	dtc_5f9b0110aad5-maxBins: 50,
	dtc_5f9b0110aad5-maxDepth: 3
}, {
	dtc_5f9b0110aad5-maxBins: 50,
	dtc_5f9b0110aad5-maxDepth: 10
}, {
	dtc_5f9b0110aad5-maxBins: 50,
	dtc_5f9b0110aad5-maxDepth: 15
})

Perform 5-fold Cross Validation.

In [0]:
%scala

// Create 5-fold CrossValidator
val cv = new CrossValidator()
  .setEstimator(dt)
  .setEvaluator(evaluator)
  .setEstimatorParamMaps(paramGrid)
  .setNumFolds(5)

// Run cross validations
val cvModel = cv.fit(trainingData)

cv: org.apache.spark.ml.tuning.CrossValidator = cv_8e8895ab4e14
cvModel: org.apache.spark.ml.tuning.CrossValidatorModel = CrossValidatorModel: uid=cv_8e8895ab4e14, bestModel=DecisionTreeClassificationModel: uid=dtc_5f9b0110aad5, depth=10, numNodes=97, numClasses=2, numFeatures=35, numFolds=5

We can print out what our Tree Model looks like using toDebugString.

In [0]:
%scala 

val bestTreeModel = cvModel.bestModel.asInstanceOf[DecisionTreeClassificationModel]
println("Learned classification tree model:\n" + bestTreeModel.toDebugString)

Learned classification tree model:
DecisionTreeClassificationModel: uid=dtc_5f9b0110aad5, depth=10, numNodes=97, numClasses=2, numFeatures=35
 If (feature 9 in {0.0,1.0,3.0})
 If (feature 5 in {0.0,1.0,2.0,3.0,4.0,5.0,6.0,7.0,8.0,9.0,10.0,11.0,12.0,13.0,14.0,16.0,17.0,19.0})
 If (feature 16 in {0.0,1.0,2.0,4.0,8.0,10.0,11.0,12.0,16.0,17.0,18.0,19.0,20.0,21.0,22.0,23.0,26.0,27.0,28.0,29.0,30.0,31.0,33.0,34.0,36.0,37.0,38.0})
 If (feature 5 in {0.0,1.0,2.0,4.0,5.0,6.0,7.0,8.0,9.0,10.0,11.0,12.0,13.0,14.0,16.0,17.0,19.0})
 Predict: 0.0
 Else (feature 5 not in {0.0,1.0,2.0,4.0,5.0,6.0,7.0,8.0,9.0,10.0,11.0,12.0,13.0,14.0,16.0,17.0,19.0})
 If (feature 4 in {0.0,1.0,2.0,3.0,6.0,7.0,9.0,10.0,13.0})
 Predict: 0.0
 Else (feature 4 not in {0.0,1.0,2.0,3.0,6.0,7.0,9.0,10.0,13.0})
 Predict: 1.0
 Else (feature 16 not in {0.0,1.0,2.0,4.0,8.0,10.0,11.0,12.0,16.0,17.0,18.0,19.0,20.0,21.0,22.0,23.0,26.0,27.0,28.0,29.0,30.0,31.0,33.0,34.0,36.0,37.0,38.0})
 If (feature 12 in {0.0,1.0,2.0,3.0,4.0,6.0})
 If (feature 5 in {0.0,1.0,3.0,6.0,7.0,9.0,14.0,16.0,17.0,19.0})
 Predict: 0.0
 Else (feature 5 not in {0.0,1.0,3.0,6.0,7.0,9.0,14.0,16.0,17.0,19.0})
 If (feature 27 <= 3.5)
 If (feature 4 in {3.0,4.0,7.0,8.0,10.0,12.0,13.0})
 Predict: 0.0
 Else (feature 4 not in {3.0,4.0,7.0,8.0,10.0,12.0,13.0})
 If (feature 7 in {0.0,2.0})
 If (feature 26 <= 21.5)
 Predict: 0.0
 Else (feature 26 > 21.5)
 If (feature 0 in {1.0})
 Predict: 0.0
 Else (feature 0 not in {1.0})
 Predict: 1.0
 Else (feature 7 not in {0.0,2.0})
 If (feature 19 <= 408516.0)
 Predict: 1.0
 Else (feature 19 > 408516.0)
 If (feature 5 in {2.0,4.0,8.0,11.0,12.0})
 Predict: 0.0
 Else (feature 5 not in {2.0,4.0,8.0,11.0,12.0})
 Predict: 1.0
 Else (feature 27 > 3.5)
 Predict: 1.0
 Else (feature 12 not in {0.0,1.0,2.0,3.0,4.0,6.0})
 If (feature 5 in {3.0,6.0,12.0,13.0,16.0,19.0})
 Predict: 0.0
 Else (feature 5 not in {3.0,6.0,12.0,13.0,16.0,19.0})
 If (feature 4 in {4.0,9.0,13.0})
 Predict: 0.0
 Else (feature 4 not in {4.0,9.0,13.0})
 Predict: 1.0
 Else (feature 5 not in {0.0,1.0,2.0,3.0,4.0,5.0,6.0,7.0,8.0,9.0,10.0,11.0,12.0,13.0,14.0,16.0,17.0,19.0})
 If (feature 16 in {7.0,29.0})
 Predict: 0.0
 Else (feature 16 not in {7.0,29.0})
 If (feature 17 <= 448.0)
 If (feature 19 <= 979753.5)
 If (feature 21 <= 786.85)
 Predict: 0.0
 Else (feature 21 > 786.85)
 If (feature 25 <= -79100.0)
 Predict: 0.0
 Else (feature 25 > -79100.0)
 Predict: 1.0
 Else (feature 19 > 979753.5)
 Predict: 0.0
 Else (feature 17 > 448.0)
 Predict: 0.0
 Else (feature 9 not in {0.0,1.0,3.0})
 If (feature 5 in {4.0,5.0,6.0,7.0,16.0,17.0})
 If (feature 16 in {1.0,3.0,5.0,7.0,8.0,9.0,10.0,11.0,13.0,14.0,16.0,17.0})
 Predict: 0.0
 Else (feature 16 not in {1.0,3.0,5.0,7.0,8.0,9.0,10.0,11.0,13.0,14.0,16.0,17.0})
 If (feature 4 in {1.0,8.0})
 Predict: 0.0
 Else (feature 4 not in {1.0,8.0})
 If (feature 11 in {4.0})
 If (feature 3 in {2.0,4.0})
 Predict: 0.0
 Else (feature 3 not in {2.0,4.0})
 Predict: 1.0
 Else (feature 11 not in {4.0})
 If (feature 21 <= 915.13)
 Predict: 0.0
 Else (feature 21 > 915.13)
 If (feature 3 in {1.0})
 If (feature 0 in {2.0})
 Predict: 0.0
 Else (feature 0 not in {2.0})
 Predict: 1.0
 Else (feature 3 not in {1.0})
 Predict: 1.0
 Else (feature 5 not in {4.0,5.0,6.0,7.0,16.0,17.0})
 If (feature 12 in {5.0})
 If (feature 4 in {0.0,3.0,8.0,9.0,11.0})
 Predict: 0.0
 Else (feature 4 not in {0.0,3.0,8.0,9.0,11.0})
 If (feature 1 in {2.0})
 Predict: 0.0
 Else (feature 1 not in {2.0})
 Predict: 1.0
 Else (feature 12 not in {5.0})
 If (feature 16 in {1.0,3.0,4.0,9.0,10.0,12.0,14.0,15.0,20.0,29.0,38.0})
 If (feature 11 in {2.0,3.0})
 If (feature 3 in {1.0,2.0,3.0,4.0,5.0,6.0})
 Predict: 0.0
 Else (feature 3 not in {1.0,2.0,3.0,4.0,5.0,6.0})
 Predict: 1.0
 Else (feature 11 not in {2.0,3.0})
 If (feature 13 in {1.0,2.0})
 If (feature 6 in {1.0,3.0,4.0})
 Predict: 0.0
 Else (feature 6 not in {1.0,3.0,4.0})
 If (feature 3 in {1.0})
 Predict: 0.0
 Else (feature 3 not in {1.0})
 Predict: 1.0
 Else (feature 13 not in {1.0,2

In [0]:
%scala

// Use test set here so we can measure the accuracy of our model on new data
val cvPredictions = cvModel.transform(testData)

cvPredictions: org.apache.spark.sql.DataFrame = [label: double, fraud_reported: string ... 43 more fields]

In [0]:
%scala

// cvModel uses the best model found from the Cross Validation
// Evaluate best model
evaluator.evaluate(cvPredictions)

res40: Double = 0.7118951612903227

Using the same evaluator as before, we can see that Cross Validation improved our model's accuracy from 0.732 to 0.841!

In [0]:
%scala

display(bestTreeModel)

treeNode {"index":41,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,3.0],"feature":9,"overflow":false} {"index":29,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,2.0,3.0,4.0,5.0,6.0,7.0,8.0,9.0,10.0,11.0,12.0,13.0,14.0,16.0,17.0,19.0],"feature":5,"overflow":false} {"index":5,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,2.0,4.0,8.0,10.0,11.0,12.0,16.0,17.0,18.0,19.0,20.0,21.0,22.0,23.0,26.0,27.0,28.0,29.0,30.0,31.0,33.0,34.0,36.0,37.0,38.0],"feature":16,"overflow":false} {"index":1,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,2.0,4.0,5.0,6.0,7.0,8.0,9.0,10.0,11.0,12.0,13.0,14.0,16.0,17.0,19.0],"feature":5,"overflow":false} {"index":0,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":3,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,2.0,3.0,6.0,7.0,9.0,10.0,13.0],"feature":4,"overflow":false} {"index":2,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":4,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":23,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,2.0,3.0,4.0,6.0],"feature":12,"overflow":false} {"index":7,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,1.0,3.0,6.0,7.0,9.0,14.0,16.0,17.0,19.0],"feature":5,"overflow":false} {"index":6,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":21,"featureType":"continuous","prediction":null,"threshold":3.5,"categories":null,"feature":27,"overflow":false} {"index":9,"featureType":"categorical","prediction":null,"threshold":null,"categories":[3.0,4.0,7.0,8.0,10.0,12.0,13.0],"feature":4,"overflow":false} {"index":8,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":15,"featureType":"categorical","prediction":null,"threshold":null,"categories":[0.0,2.0],"feature":7,"overflow":false} {"index":11,"featureType":"continuous","prediction":null,"threshold":21.5,"categories":null,"feature":26,"overflow":false} {"index":10,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":13,"featureType":"categorical","prediction":null,"threshold":null,"categories":[1.0],"feature":0,"overflow":false} {"index":12,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":14,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":17,"featureType":"continuous","prediction":null,"threshold":408516.0,"categories":null,"feature":19,"overflow":false} {"index":16,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":19,"featureType":"categorical","prediction":null,"threshold":null,"categories":[2.0,4.0,8.0,11.0,12.0],"feature":5,"overflow":false} {"index":18,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":20,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":22,"featureType":null,"prediction":1.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":25,"featureType":"categorical","prediction":null,"threshold":null,"categories":[3.0,6.0,12.0,13.0,16.0,19.0],"feature":5,"overflow":false} {"index":24,"featureType":null,"prediction":0.0,"threshold":null,"categories":null,"feature":null,"overflow":false} {"index":27,"featureType":"categorical","prediction":null,"threshold":null,"categories":[4.0,9.0,13.0],"feature":4,"overflow":false} {"index":26,"featureType":null,"prediction":0.0,"

In [0]:
%scala

println(bestTreeModel.featureImportances)

(35,[0,1,3,4,5,6,7,9,11,12,13,15,16,17,19,21,25,26,27,34],[0.011780543390830277,0.006731739080474446,0.03585056990059972,0.06810761062416765,0.2623134450444737,0.027701499985104416,0.010409996512681397,0.29546369665156424,0.03673315050672274,0.03961488336858072,0.01339261774957548,0.032383107343657305,0.07776627791078593,0.00642092680311017,0.023542387506437043,0.01994199547725066,0.00762270454700784,0.003464865703185374,0.011603140010504394,0.009154841883286418])

We know that feature 9 is our Decision Tree model's root node and that 5 is a close 2nd in importance. Let's see what they correspond to.

In [0]:
print (assemblerInputs[9])
print (assemblerInputs[5])

incident_severityIndex
insured_hobbiesIndex

Turns out that incident severity and insured hobbies are the best predictors for whether an insurance claim is fraudulent or not!

## Zooming in on Prediction Data

We can further analyze the resulting prediction data. As an example, we can view an estimate of what our total predicted fradulent claim amount is like, and zoom into a breakdown of predicted fraud count by incident severity and insured hobbies since those our model's best predictors.

Lets hop back to Python for this.

In [0]:
%scala

cvPredictions.createOrReplaceTempView("cvPredictions")

In [0]:
# Select columns to zoom into (In this example: Total Claim Amount and Auto Make)
# Filter for data points that were predicted to be Fraud cases
cvPredictions = sqlContext.sql("SELECT * FROM cvPredictions")
incidentSeverityDF = cvPredictions.select("prediction", "total_claim_amount", "incident_severity").filter("prediction = 1")
insuredHobbiesDF = cvPredictions.select("prediction", "total_claim_amount", "insured_hobbies").filter("prediction = 1")

In [0]:
# View Count of Predicted Fraudulent Claims by Incident Severity
display(incidentSeverityDF)

prediction total_claim_amount incident_severity 1.0 74700 Total Loss 1.0 66780 Major Damage 1.0 51600 Major Damage 1.0 77100 Total Loss 1.0 52380 Major Damage 1.0 64260 Total Loss 1.0 58300 Major Damage 1.0 83490 Minor Damage 1.0 54900 Major Damage 1.0 71060 Major Damage 1.0 83160 Major Damage 1.0 44640 Major Damage 1.0 61490 Total Loss 1.0 38610 Major Damage 1.0 5700 Trivial Damage 1.0 5900 Minor Damage 1.0 79750 Major Damage 1.0 48060 Major Damage 1.0 69850 Major Damage 1.0 52800 Total Loss 1.0 46860 Major Damage 1.0 46980 Major Damage 1.0 84590 Total Loss 1.0 76400 Major Damage 1.0 70900 Major Damage 1.0 58410 Major Damage 1.0 69300 Major Damage 1.0 52560 Major Damage 1.0 75460 Total Loss 1.0 48360 Minor Damage 1.0 62300 Major Damage 1.0 76010 Minor Damage 1.0 71280 Major Damage 1.0 75400 Total Loss 1.0 80850 Major Damage 1.0 46800 Major Damage 1.0 74360 Total Loss 1.0 36720 Major Damage 1.0 53820 Major Damage 1.0 42700 Major Damage 1.0 85900 Major Damage 1.0 54360 Major Damage 1.0 81840 Minor Damage 1.0 51390 Minor Damage 1.0 40700 Minor Damage 1.0 6400 Trivial Damage 1.0 57690 Major Damage 1.0 62880 Total Loss 1.0 72400 Major Damage 1.0 55440 Major Damage 1.0 53730 Minor Damage 1.0 64800 Total Loss 1.0 5000 Trivial Damage 1.0 64350 Major Damage 1.0 47760 Major Damage 1.0 59400 Total Loss 1.0 71760 Major Damage 1.0 79800 Major Damage 1.0 60750 Major Damage 1.0 47630 Major Damage 1.0 57240 Total Loss 1.0 35860 Total Loss 1.0 78650 Total Loss 1.0 4620 Minor Damage 1.0 75570 Major Damage 1.0 55200 Major Damage 1.0 73920 Major Damage 1.0 63120 Major Damage 1.0 45120 Major Damage 1.0 5720 Minor Damage 1.0 74800 Major Damage 1.0 90860 Major Damage 1.0 98160 Total Loss 1.0 67300 Major Damage

In [0]:
# View Count of Predicted Fraudulent Claims by Insured Hobbies
display(insuredHobbiesDF)

prediction total_claim_amount insured_hobbies 1.0 74700 paintball 1.0 66780 sleeping 1.0 51600 reading 1.0 77100 polo 1.0 52380 camping 1.0 64260 chess 1.0 58300 board-games 1.0 83490 chess 1.0 54900 sleeping 1.0 71060 reading 1.0 83160 reading 1.0 44640 base-jumping 1.0 61490 chess 1.0 38610 exercise 1.0 5700 bungie-jumping 1.0 5900 golf 1.0 79750 paintball 1.0 48060 polo 1.0 69850 sleeping 1.0 52800 exercise 1.0 46860 exercise 1.0 46980 base-jumping 1.0 84590 golf 1.0 76400 paintball 1.0 70900 skydiving 1.0 58410 camping 1.0 69300 chess 1.0 52560 exercise 1.0 75460 board-games 1.0 48360 golf 1.0 62300 bungie-jumping 1.0 76010 chess 1.0 71280 board-games 1.0 75400 cross-fit 1.0 80850 yachting 1.0 46800 video-games 1.0 74360 cross-fit 1.0 36720 base-jumping 1.0 53820 skydiving 1.0 42700 reading 1.0 85900 polo 1.0 54360 dancing 1.0 81840 cross-fit 1.0 51390 chess 1.0 40700 chess 1.0 6400 chess 1.0 57690 cross-fit 1.0 62880 chess 1.0 72400 yachting 1.0 55440 skydiving 1.0 53730 chess 1.0 64800 cross-fit 1.0 5000 chess 1.0 64350 exercise 1.0 47760 hiking 1.0 59400 chess 1.0 71760 paintball 1.0 79800 movies 1.0 60750 basketball 1.0 47630 bungie-jumping 1.0 57240 cross-fit 1.0 35860 chess 1.0 78650 cross-fit 1.0 4620 chess 1.0 75570 video-games 1.0 55200 bungie-jumping 1.0 73920 hiking 1.0 63120 movies 1.0 45120 exercise 1.0 5720 chess 1.0 74800 paintball 1.0 90860 board-games 1.0 98160 chess 1.0 67300 video-games

Looks like people who are in major accidents and play chess or are into cross-fit are more prone to committing fraud.

###Gradient Boosting Trees and Random Forest
###Modeling and Evaluation

In [0]:
%scala

import org.apache.spark.ml.classification.{GBTClassifier, GBTClassificationModel}

// Create initial Decision Tree Model
val gbt = new GBTClassifier()
  .setLabelCol("label")
  .setFeaturesCol("features")
  .setMaxDepth(5)
  .setMaxBins(40)

// Train model with Training Data
val gbtModel = gbt.fit(trainingData)

// Make predictions on test data using the transform() method.
// .transform() will only use the 'features' column as input.
val gbtPredictions = gbtModel.transform(testData)

import org.apache.spark.ml.classification.{GBTClassifier, GBTClassificationModel}
gbt: org.apache.spark.ml.classification.GBTClassifier = gbtc_f49e728b5174
gbtModel: org.apache.spark.ml.classification.GBTClassificationModel = GBTClassificationModel: uid = gbtc_f49e728b5174, numTrees=20, numClasses=2, numFeatures=35
gbtPredictions: org.apache.spark.sql.DataFrame = [label: double, fraud_reported: string ... 43 more fields]

In [0]:
%scala

import org.apache.spark.ml.classification.{RandomForestClassifier, RandomForestClassificationModel}

// Create initial Decision Tree Model
val rf = new RandomForestClassifier()
  .setLabelCol("label")
  .setFeaturesCol("features")
  .setMaxDepth(5)
  .setMaxBins(40)

// Train model with Training Data
val rfModel = rf.fit(trainingData)

// Make predictions on test data using the transform() method.
// .transform() will only use the 'features' column as input.
val rfPredictions = rfModel.transform(testData)

import org.apache.spark.ml.classification.{RandomForestClassifier, RandomForestClassificationModel}
rf: org.apache.spark.ml.classification.RandomForestClassifier = rfc_0398bc8d9a9e
rfModel: org.apache.spark.ml.classification.RandomForestClassificationModel = RandomForestClassificationModel: uid=rfc_0398bc8d9a9e, numTrees=20, numClasses=2, numFeatures=35
rfPredictions: org.apache.spark.sql.DataFrame = [label: double, fraud_reported: string ... 43 more fields]

In [0]:
%scala
println("GBT Eval - " + evaluator.evaluate(gbtPredictions))
println("RF Eval - " + evaluator.evaluate(rfPredictions))

GBT Eval - 0.8233294930875581
RF Eval - 0.8354262672811066